# Exploratory Data Analysis & Preprocessing

This notebook performs comprehensive exploratory data analysis (EDA) and data preprocessing for the SECOM semiconductor manufacturing dataset.

> Objectives:
- Load and explore the SECOM dataset (1567 samples, 591 features)
- Analyze missing value patterns and data quality
- Perform statistical analysis and visualization
- Clean and preprocess data for machine learning
- Save cleaned dataset for downstream analysis

> Dataset Information:
- **Source**: UCI ML Repository - SECOM Dataset
- **Samples**: 1,567 wafers
- **Features**: 591 sensor measurements and process parameters
- **Target**: Binary classification (–1: pass and 1: fail)
- **Challenge**: High missing value rate (41951/924530 (4.54%) missing values)

---

> Why SECOM dataset has so many missing values?
The SECOM dataset contains a large number of missing values primarily due to the nature of semiconductor manufacturing processes. Several factors contribute to this:
  1. **Sensor Failures**: Thousands of sensors used across processes like deposition, etching, and lithography, some may malfunction or fail, leading to gaps in data collection.
  2. **Process Variability**: Different wafers may go through different processing steps, resulting in some sensors not being applicable or used for certain wafers.
  3. **Data Logging Issues**: There may be issues in data logging systems that lead to incomplete records.
  4. **Intentional Omissions**: Some data points may be intentionally left out if they are being recalibrated, deemed irrelevant or redundant for specific wafers.
  5. **Complex Manufacturing Environment**: The complexity and scale of semiconductor manufacturing can lead to inconsistencies in data collection.

In [1]:
# Import required libraries 
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import networkx as nx
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import warnings
warnings.filterwarnings('ignore')

# Set plotting style
plt.style.use('seaborn-v0_8')
sns.set_palette("husl")

# Import our utility functions
import sys
import os
notebook_path = os.path.abspath("")
if notebook_path.endswith("notebooks"):
    project_root = os.path.dirname(notebook_path)
    os.chdir(project_root)
from app.utils import load_data, preprocess_data, get_data_summary

pd.set_option('display.width', 300)
# pd.set_option('display.max_rows', None)

print("Libraries imported successfully!")
print("Ready to begin EDA and preprocessing...")
print(f"Working directory set to: {os.getcwd()}")

Libraries imported successfully!
Ready to begin EDA and preprocessing...
Working directory set to: c:\Users\KarMing\Documents\wafer-yield


## 1. Data Loading and Initial Exploration


In [2]:
# Load the SECOM dataset
data = load_data()

# Display basic information
print(f"\nDataset shape: {data.shape}")
print(f"Memory usage: {data.memory_usage(deep=True).sum() / 1024**2:.2f} MB")
print(f"\nData types:")
print(data.dtypes.value_counts())

# Temporary drop timestamp column
if 'timestamp' in data.columns:
    data_timestamp = data['timestamp']
    data = data.drop(columns=['timestamp'])

# Display first few rows
print(f"\nFirst 5 rows:")
data.head()



= Loading raw SECOM data...

Dataset shape: (1567, 592)
Memory usage: 7.17 MB

Data types:
float64    590
int64        1
object       1
Name: count, dtype: int64

First 5 rows:


feature_0  feature_1  feature_2  feature_3  feature_4  feature_5  feature_6  feature_7  feature_8  feature_9  ...  feature_581  feature_582  feature_583  feature_584  feature_585  feature_586  feature_587  feature_588  feature_589  target
0    3030.93    2564.00  2187.7333  1411.1265     1.3602      100.0    97.6133     0.1242     1.5005     0.0162  ...          NaN       0.5005       0.0118       0.0035       2.3630          NaN          NaN          NaN          NaN      -1
1    3095.78    2465.14  2230.4222  1463.6606     0.8294      100.0   102.3433     0.1247     1.4966    -0.0005  ...     208.2045       0.5019       0.0223       0.0055       4.4447       0.0096       0.0201       0.0060     208.2045      -1
2    2932.61    2559.94  2186.4111  1698.0172     1.5102      100.0    95.4878     0.1241     1.4436     0.0041  ...      82.8602       0.4958       0.0157       0.0039       3.1745       0.0584       0.0484       0.0148      82.8602       1
3    2988.72    2479.90  2199.0333   909.7926     1.3204      100.0   104.2367     0.1217     1.4882    -0.0124  ...      73.8432       0.4990       0.0103       0.0025       2.0544       0.0202       0.0149       0.0044      73.8432      -1
4    3032.24    2502.87  2233.3667  1326.5200     1.5334      100.0   100.3967     0.1235     1.5031    -0.0031  ...          NaN       0.4800       0.4766       0.1045      99.3032       0.0202       0.0149       0.0044      73.8432      -1

[5 rows x 591 columns]

In [3]:
# Get comprehensive data summary
# Q: Why?
# A: To quickly profile the dataset before deeper EDA.
summary = get_data_summary(data)
print("= Dataset Summary:")
for key, value in summary.items():
    print(f"> {key}: {value}")

# Check for target variable
if 'target' in data.columns:
    print(f"\nTarget variable distribution:")
    print(data['target'].value_counts())
    print(f"Class balance ratio: {summary.get('class_balance', 'N/A'):.3f}")
else:
    print("\nNo target variable found in dataset")

= Dataset Summary:
> n_samples: 1567
> n_features: 590
> missing_values: 41951
> missing_percentage: 4.5298710610227655
> target_distribution: {-1: 1463, 1: 104}
> class_balance: 0.0710868079289132

Target variable distribution:
target
-1    1463
 1     104
Name: count, dtype: int64
Class balance ratio: 0.071


> Limitations / missing pieces to consider

- No hyperparameter tuning / nested CV; the RF uses fixed n_estimators=200.
- No calibration / threshold selection / confusion matrices or class‑specific metrics beyond averaged precision/recall/f1.
- Mapping y → {0,1} is fine for modeling but if downstream code expects -1/1 you must keep track of the mapping.
- If you want per‑class metrics (precision_recall_fscore_support) or PR curve for the minority class, add those.
- SMOTE is used with default params — consider tuning k_neighbors or trying other resamplers (ADASYN, borderline‑SMOTE) and compare with undersampling/ensemble methods.
- For rigorous comparison use nested CV or a repeated stratified CV and record training vs test scores to check overfitting.

---

## 2. Missing Value Analysis

> Why is it important to analyze missing values?
Analyzing missing values is crucial because:
1. **Data Quality**: High rates of missing data can indicate issues with data collection processes
2. **Bias**: Missing data can introduce bias if the missingness is not random, affecting model performance.
3. **Imputation Strategies**: Understanding the pattern of missingness helps in choosing appropriate imputation methods.
4. **Feature Selection**: Features with excessive missing values may need to be excluded from analysis.

> Steps:

0. Look at correlation of missingness between features (heatmap) to see if some sensors fail together.
- If corr > 0.98, they always go missing together → likely redundant → can drop one later.

1. Quantify missing values per feature
- Get 28 features with >50% missing values, 8 with >80%
- Focus on >80% first (don't drop yet)

2. For those 8 features, look for patterns
- Check if missing values occur together — e.g., 3 sensors always missing in the same wafers
- Missing randomly (no clear group)	→ Probably not important → can drop later
- Missing in groups or by process stage	→ Likely meaningful → keep and investigate (Step 3)

3. Check if Missingness Predicts Wafer Yield
- Check if missing values are more common in failed wafers.
- Example: If sensor_45 is missing more often when wafer = fail → that’s useful signal.
- We want to know if “being missing” is actually predicting the wafer yield.
- If yes → don’t drop it!
- Missing values are related to yield (p < 0.05) → Keep feature + create missing flag
- No relationship (p > 0.05) → Can drop if >80% missing

4. Choose to Drop, Flag, or Fill (Impute)

---

### 2.1 Keep Only One of Highly Correlated Missingness Features
> For all those features that has high correlation of missingness, only keep one of them

In [4]:
# Calculate missing value statistics (focus on columns that have missing values only)
features = [col for col in data.columns if col != 'target']
data_features = data[features]

# Columns with missing values
cols_with_missing = data_features.columns[data_features.isnull().any()]
cols_without_missing = data_features.columns[~data_features.isnull().any()]
print(f"\nColumns with missing values ({len(cols_with_missing)}): {list(cols_with_missing)}")
print(f"Columns without missing values ({len(cols_without_missing)}): {list(cols_without_missing)}")

missing_corr = data_features[cols_with_missing].isnull().corr()
# Plotly heatmap
fig = px.imshow(
    missing_corr,
    text_auto=False,  # change to True if you want correlation values displayed
    color_continuous_scale='RdBu',
    zmin=-1,
    zmax=1,
    title='Missingness Correlation'
)

fig.update_layout(
    width=900,
    height=800,
    xaxis_title='Features',
    yaxis_title='Features'
)

fig.show()


Columns with missing values (538): ['feature_0', 'feature_1', 'feature_2', 'feature_3', 'feature_4', 'feature_5', 'feature_6', 'feature_7', 'feature_8', 'feature_9', 'feature_10', 'feature_11', 'feature_12', 'feature_13', 'feature_14', 'feature_15', 'feature_16', 'feature_17', 'feature_18', 'feature_19', 'feature_21', 'feature_22', 'feature_23', 'feature_24', 'feature_25', 'feature_26', 'feature_27', 'feature_28', 'feature_29', 'feature_30', 'feature_31', 'feature_32', 'feature_33', 'feature_34', 'feature_35', 'feature_36', 'feature_37', 'feature_38', 'feature_39', 'feature_40', 'feature_41', 'feature_42', 'feature_43', 'feature_44', 'feature_45', 'feature_46', 'feature_47', 'feature_48', 'feature_49', 'feature_50', 'feature_51', 'feature_52', 'feature_53', 'feature_54', 'feature_55', 'feature_56', 'feature_57', 'feature_58', 'feature_59', 'feature_60', 'feature_61', 'feature_62', 'feature_63', 'feature_64', 'feature_65', 'feature_66', 'feature_67', 'feature_68', 'feature_69', 'featur

In [5]:
# Check for different thresholds
def analyze_missing_corr_thresholds(missing_corr, thresholds=[0.5, 0.8, 0.9, 0.95, 0.99]):
    results = []

    for threshold in thresholds:
        high_corr_features = set()
        for i in range(len(missing_corr.columns)):
            for j in range(i):
                if abs(missing_corr.iloc[i, j]) > threshold and missing_corr.columns[i] != missing_corr.columns[j]:
                    high_corr_features.add((missing_corr.columns[i], missing_corr.columns[j]))

        G = nx.Graph()
        G.add_edges_from(high_corr_features)
        correlated_groups = list(nx.connected_components(G))

        # Count how many features you’d drop if you keep 1 per group
        drop_count = sum(len(g) - 1 for g in correlated_groups)
        keep_count = len(missing_corr.columns) - drop_count

        results.append({
            "Threshold": threshold,
            "Num_Groups": len(correlated_groups),
            "Keep_Features": keep_count,
            "Drop_Features": drop_count,
        })

    return pd.DataFrame(results)

# Example usage
threshold_analysis = analyze_missing_corr_thresholds(missing_corr)
print(threshold_analysis)


   Threshold  Num_Groups  Keep_Features  Drop_Features
0       0.50          28             28            510
1       0.80          32             32            506
2       0.90          33             33            505
3       0.95          35             35            503
4       0.99          35             35            503


In [6]:
# Get a list of features that missing correlate with each other
threshold = 0.90

high_corr_features = set()
for i in range(len(missing_corr.columns)):
    for j in range(i):
        if abs(missing_corr.iloc[i, j]) > threshold and missing_corr.columns[i] != missing_corr.columns[j]:
            high_corr_features.add((missing_corr.columns[i], missing_corr.columns[j]))
print(f"\nFeatures with missingness correlation > {threshold}:")
for feat_pair in high_corr_features:
    print(feat_pair, "Value: ", missing_corr.loc[feat_pair[0], feat_pair[1]])


Features with missingness correlation > 0.9:
('feature_262', 'feature_128') Value:  1.0
('feature_403', 'feature_262') Value:  1.0
('feature_530', 'feature_256') Value:  1.0
('feature_407', 'feature_397') Value:  0.9425066168616671
('feature_399', 'feature_396') Value:  1.0
('feature_440', 'feature_31') Value:  1.0
('feature_334', 'feature_203') Value:  1.0
('feature_565', 'feature_562') Value:  1.0
('feature_423', 'feature_151') Value:  1.0
('feature_555', 'feature_554') Value:  1.0
('feature_354', 'feature_118') Value:  1.0
('feature_541', 'feature_406') Value:  1.0
('feature_262', 'feature_130') Value:  1.0
('feature_461', 'feature_50') Value:  1.0
('feature_480', 'feature_478') Value:  1.0
('feature_371', 'feature_237') Value:  1.0
('feature_263', 'feature_134') Value:  0.942506616861667
('feature_435', 'feature_297') Value:  1.0
('feature_199', 'feature_61') Value:  1.0
('feature_468', 'feature_61') Value:  0.9255235051470415
('feature_443', 'feature_34') Value:  1.0
('feature_15

In [7]:
# Build a graph of correlated features
G = nx.Graph()
G.add_edges_from(high_corr_features)

# Find connected components (clusters of correlated features)
correlated_groups = list(nx.connected_components(G))

# Optional: view the groups for transparency
for group in correlated_groups:
    print("Group:", group)

# Create lists to store decisions
features_to_keep = []
features_to_drop = []

summary_records = []

for idx, group in enumerate(correlated_groups, start=1):
    group = sorted(list(group))  # sort for reproducibility
    keep_feature = data_features[group].isnull().mean().idxmin()
    drop_features = group[1:]
    
    features_to_keep.append(keep_feature)
    features_to_drop.extend(drop_features)
    
    summary_records.append({
        "Group": idx,
        "Kept Feature": keep_feature,
        "Dropped Count": len(drop_features),
        "Dropped Features": ", ".join(drop_features)
    })

# Convert summary to DataFrame for nice viewing
summary_df = pd.DataFrame(summary_records)

print(f"✅ Number of groups found: {len(correlated_groups)}")
print(f"✅ Features kept: {len(features_to_keep)}")
print(f"✅ Features dropped: {len(features_to_drop)}")

# Drop the features from the original data
data_reduced_cols_with_missing = data[cols_with_missing].drop(columns=features_to_drop)
data_reduced_cols_with_missing.shape

Group: {'feature_122', 'feature_266', 'feature_407', 'feature_533', 'feature_399', 'feature_263', 'feature_262', 'feature_128', 'feature_267', 'feature_264', 'feature_269', 'feature_133', 'feature_404', 'feature_535', 'feature_529', 'feature_536', 'feature_531', 'feature_539', 'feature_528', 'feature_395', 'feature_402', 'feature_530', 'feature_130', 'feature_261', 'feature_123', 'feature_125', 'feature_534', 'feature_397', 'feature_256', 'feature_126', 'feature_134', 'feature_259', 'feature_268', 'feature_540', 'feature_124', 'feature_400', 'feature_265', 'feature_541', 'feature_403', 'feature_394', 'feature_129', 'feature_405', 'feature_398', 'feature_131', 'feature_537', 'feature_258', 'feature_406', 'feature_132', 'feature_121', 'feature_396', 'feature_257', 'feature_127', 'feature_532', 'feature_260', 'feature_538', 'feature_401'}
Group: {'feature_300', 'feature_430', 'feature_161', 'feature_295', 'feature_28', 'feature_435', 'feature_26', 'feature_168', 'feature_299', 'feature_29

(1567, 33)

In [8]:
# Look at the heatmap again after dropping correlated features
reduced_missing_corr = data_reduced_cols_with_missing.isnull().corr()
fig = px.imshow(
    reduced_missing_corr,
    text_auto=True,  # change to True if you want correlation values displayed
    color_continuous_scale='RdBu',
    zmin=-1,
    zmax=1,
    title='Missingness Correlation After Dropping Correlated Features'
)

fig.update_layout(
    width=900,
    height=800,
    xaxis_title='Features',
    yaxis_title='Features'
)

fig.show()

> Revise the new data after dropping correlated features with missingness


In [9]:
# Look at the new data shape
print("Cols with missing after reduced: ", data_reduced_cols_with_missing.shape)

# Concat with columns that had no missing values
data_reduced = pd.concat([data_reduced_cols_with_missing, data[cols_without_missing]], axis=1)
print("New data shape: ", data_reduced.shape)

# Brief look at the new data summary
reduced_summary = get_data_summary(data_reduced)
print("= Reduced Dataset Summary:")
for key, value in reduced_summary.items():
    print(f"> {key}: {value}")

# Head of the reduced data
data_reduced.head()

Cols with missing after reduced:  (1567, 33)
New data shape:  (1567, 85)
= Reduced Dataset Summary:
> n_samples: 1567
> n_features: 85
> missing_values: 6984
> missing_percentage: 5.243440069071662


feature_0  feature_1  feature_10  feature_13  feature_100  feature_103  feature_109  feature_112  feature_118  feature_121  ...  feature_526  feature_527  feature_570  feature_571  feature_572  feature_573  feature_574  feature_575  feature_576  feature_577
0    3030.93    2564.00     -0.0034         0.0       0.0002      -0.0042          NaN          NaN       0.6002        15.88  ...       0.5064       6.6926     533.8500       2.1113         8.95       0.3157       3.0624       0.1026       1.6765      14.9509
1    3095.78    2465.14     -0.0148         0.0      -0.0004      -0.0045          NaN          NaN       0.5958        15.88  ...       0.8832       8.8370     535.0164       2.4335         5.92       0.2653       2.0111       0.0772       1.1065      10.9003
2    2932.61    2559.94      0.0013         0.0       0.0006      -0.0026          NaN       0.4684       0.6015        15.90  ...       0.6451       6.4568     535.0245       2.0293        11.21       0.1882       4.0923       0.0640       2.0952       9.2721
3    2988.72    2479.90     -0.0033         0.0      -0.0002      -0.0059          NaN       0.4647       0.6016        15.55  ...       0.7404       6.4865     530.5682       2.0253         9.33       0.1738       2.8971       0.0525       1.7585       8.5831
4    3032.24    2502.87     -0.0072         0.0       0.0004      -0.0045          NaN          NaN       0.5913        15.75  ...       2.2181       6.3745     532.0155       2.0275         8.83       0.2224       3.1776       0.0706       1.6597      10.9698

[5 rows x 85 columns]

> Look at some stats of data_reduced

In [10]:
missing_stats = data_reduced.isnull().sum()
missing_percentage = (missing_stats / len(data_reduced)) * 100

# Create missing value summary
missing_summary = pd.DataFrame({
    'Feature': missing_stats.index,
    'Missing_Count': missing_stats.values,
    'Missing_Percentage': missing_percentage.values
}).sort_values('Missing_Percentage', ascending=False)

print("Missing Value Analysis:")
print(f"Data Shape: {data_reduced.shape}")
print(f"\nFeatures with no missing values: {len(missing_summary[missing_summary['Missing_Percentage'] == 0])}")
print(f"Features with >0% missing values: {len(missing_summary[missing_summary['Missing_Percentage'] != 0])}")
print(f"Features with >15% missing values: {len(missing_summary[missing_summary['Missing_Percentage'] > 15])}")
print(f"Features with >50% missing values: {len(missing_summary[missing_summary['Missing_Percentage'] > 50])}")
print(f"Features with >80% missing values: {len(missing_summary[missing_summary['Missing_Percentage'] > 80])}")

# Display top 10 features with most missing values
print(f"\nTop 10 features with most missing values:")
missing_summary.head(10)

Missing Value Analysis:
Data Shape: (1567, 85)

Features with no missing values: 52
Features with >0% missing values: 33
Features with >15% missing values: 8
Features with >50% missing values: 5
Features with >80% missing values: 2

Top 10 features with most missing values:


Feature  Missing_Count  Missing_Percentage
14  feature_157           1429           91.193363
23  feature_220           1341           85.577537
6   feature_109           1018           64.964901
30  feature_578            949           60.561583
25  feature_345            794           50.670070
7   feature_112            715           45.628590
29  feature_562            273           17.421825
27  feature_546            260           16.592214
24  feature_224             51            3.254627
8   feature_118             24            1.531589

In [11]:
# Create 3x1 interactive subplot grid
fig = make_subplots(
    rows=3, cols=1,
    subplot_titles=(
        'Distribution of Missing Values Across Features',
        'Top 30 Features with Most Missing Values',
        'Cumulative Histogram of Missing Percentages',
    ),
    horizontal_spacing=0.12,
    vertical_spacing=0.1
)

# 1. Missing value distribution
fig.add_trace(
    go.Histogram(
        x=missing_percentage,
        nbinsx=100,
        marker_color='skyblue',
        opacity=0.7,
        name='Missing %',
        hovertemplate='Missing %: <b>%{x:.2f}</b><br>Feature Count: %{y}<extra></extra>'
    ),
    row=1, col=1
)
fig.add_vline(x=15, line_dash='dash', line_color='red', annotation_text='15% threshold', row=1, col=1)
fig.add_vline(x=50, line_dash='dash', line_color='red', annotation_text='50% threshold', row=1, col=1)
fig.add_vline(x=80, line_dash='dash', line_color='red', annotation_text='80% threshold', row=1, col=1)

# 2️. Top 30 features with most missing values
top_missing = missing_summary.head(30)
fig.add_trace(
    go.Bar(
        y=top_missing['Missing_Percentage'],
        x=top_missing['Feature'],
        marker_color='coral',
        name='Top Missing Features',
        hovertemplate='Feature: <b>%{x}</b><br>Missing %: %{y:.2f}<extra></extra>'
    ),
    row=2, col=1
)

# 3️. Cumulative histogram of missing percentages
fig.add_trace(
    go.Histogram(
        x=missing_percentage,
        # nbinsx=100,
        marker_color='mediumseagreen',
        marker=dict(
            color='mediumseagreen',
            line=dict(
                color='black',  # outline color
                width=1          # outline thickness
            )
        ),
        opacity=0.7,
        cumulative_enabled=True,
        name='Cumulative Distribution',
        hovertemplate='Missing % ≤ %{x:.3f}<br>Cumulative Features: %{y}<extra></extra>'
    ),
    row=3, col=1
)

# Update layout for better aesthetics
fig.update_layout(
    title_text='Interactive Missing Value Analysis Dashboard',
    template='plotly_white',
    height=1500,
    width=1300,
    showlegend=False
)

# Update axes labels
fig.update_xaxes(title_text='Missing Percentage', row=1, col=1)
fig.update_yaxes(title_text='Number of Features', row=1, col=1)

fig.update_xaxes(title_text='Features', row=2, col=1)
fig.update_yaxes(title_text='Missing Percentage', row=2, col=1)

fig.update_xaxes(title_text='Missing Percentage', row=3, col=1)
fig.update_yaxes(title_text='Cumulative Features', row=3, col=1)

fig.show()

---

### 2.2 Drop, Flag or Impute
> For data_reduced, what missingness means now? Look at MCAR, MAR, MNAR

| Missingness Type                    |Meaning | What It Usually Means in Wafer Data                                                     |
| ----------------------------------- | ------ |--------------------------------------------------------------------------------------- |
| MCAR (Missing Completely at Random) | Missingness not linked to the target or feature — fault_rate(missing) ≈ fault_rate(not missing) | Sensor temporarily not recorded (e.g., network glitch) — can safely impute.             |
| MAR (Missing at Random)             | Missingness depends on *other observed* variables (not target) — can’t tell from this table alone | Missing because certain process step didn’t apply (e.g., skipped test for some wafers). |
| MNAR (Missing Not at Random)        | Missingness directly linked to the *target* (here, failure rate changes when missing) | Missing **due to fault/anomaly** — strong signal of defect risk.                        |

> Quantify “how missingness relates to target”
- Look at the data above, we have 8 features with >15% missing values. 9th feature is 3% missing, which is not that high.
- For these 8 features, we will check if missingness relates to target (wafer yield).

In [12]:
# Collect all aggregated results in one list
results = []

for col in missing_summary.loc[missing_summary['Missing_Percentage'] > 15, 'Feature'].tolist():
    temp_df = data.copy()
    temp_df['is_missing'] = temp_df[col].isnull()
    
    # Compute fault rate (proportion of target == 1)
    agg_df = (
        temp_df.groupby('is_missing', as_index=False)
        .apply(lambda x: pd.Series({
            'fault_rate': (x['target'] == 1).mean(),
            'count': len(x)
        }))
    )
    agg_df['Feature'] = col  # Add feature name for grouping
    results.append(agg_df)

# Combine all features into a single DataFrame
final_df = pd.concat(results, ignore_index=True)
print(final_df)

# Create a single grouped bar plot
fig = px.bar(
    final_df,
    x='Feature',
    y='fault_rate',
    color='is_missing',
    barmode='group',
    text='count',
    title='Fault rate (target=1) vs Missingness across features',
    labels={'fault_rate': 'Fault Rate', 'Feature': 'Feature', 'is_missing': 'Missing'}
)

# Improve readability
fig.update_traces(texttemplate='n=%{text}', textposition='outside')
fig.update_yaxes(range=[0, 1])
fig.update_layout(
    xaxis_tickangle=-45,
    legend_title_text='Is Missing',
    height=600
)

fig.show()

    is_missing  fault_rate   count      Feature
0        False    0.057971   138.0  feature_157
1         True    0.067180  1429.0  feature_157
2        False    0.048673   226.0  feature_220
3         True    0.069351  1341.0  feature_220
4        False    0.054645   549.0  feature_109
5         True    0.072692  1018.0  feature_109
6        False    0.072816   618.0  feature_578
7         True    0.062171   949.0  feature_578
8        False    0.087969   773.0  feature_345
9         True    0.045340   794.0  feature_345
10       False    0.083333   852.0  feature_112
11        True    0.046154   715.0  feature_112
12       False    0.061824  1294.0  feature_562
13        True    0.087912   273.0  feature_562
14       False    0.065800  1307.0  feature_546
15        True    0.069231   260.0  feature_546


In [13]:
from scipy.stats import chi2_contingency

for col in missing_summary.loc[missing_summary['Missing_Percentage'] > 15, 'Feature'].tolist():
    contingency = pd.crosstab(data_reduced[col].isnull(), data['target'])
    chi2, p, _, _ = chi2_contingency(contingency)
    print(f"{col}: p={p:.4f}")


feature_157: p=0.8135
feature_220: p=0.3121
feature_109: p=0.2067
feature_578: p=0.4694
feature_345: p=0.0010
feature_112: p=0.0045
feature_562: p=0.1499
feature_546: p=0.9469


| Feature         | Δ      | p          | Mechanism           | Reasoning                                               |
| --------------- | ------ | ---------- | ------------------- | ------------------------------------------------------- |
| **feature_157** | +0.009 | 0.8135     | **MCAR**            | Tiny Δ, p≫0.05 → no link to target                      |
| **feature_220** | +0.021 | 0.3121     | **Weak MNAR / MAR** | Small Δ, p>0.05 → slight trend but not significant      |
| **feature_109** | +0.018 | 0.2067     | **Weak MNAR / MAR** | Similar mild difference, not significant                |
| **feature_578** | –0.011 | 0.4694     | **MCAR**            | No significant effect                                   |
| **feature_345** | –0.043 | **0.0010** | **MNAR (inverse)**  | Large Δ + significant → strong dependence on target     |
| **feature_112** | –0.037 | **0.0045** | **MNAR (inverse)**  | Same pattern — missingness linked to lower failure rate |
| **feature_562** | +0.026 | 0.1499     | **Weak MNAR**       | Moderate Δ, not significant but close — keep flag       |
| **feature_546** | +0.003 | 0.9469     | **MCAR**            | Flat difference, no statistical relation                |


| Category                    | Features                              | Notes                                                                                                                 |
| --------------------------- | ------------------------------------- | --------------------------------------------------------------------------------------------------------------------- |
| 🟩 **MCAR**                 | feature_157, feature_578, feature_546 | Missingness independent of target — safe to impute/drop.                                                              |
| 🟧 **Weak MAR / Weak MNAR** | feature_220, feature_109, feature_562 | Slight fault-rate difference; could depend on other vars; consider keeping missing flag if modeling benefit observed. |
| 🟥 **MNAR (strong)**        | feature_345, feature_112              | Significant + large effect → strong MNAR signal (missingness tied to *lower* fault rates). Keep missing flags.        |


In [14]:
# Look again on missing summary
missing_summary.head(8)

Feature  Missing_Count  Missing_Percentage
14  feature_157           1429           91.193363
23  feature_220           1341           85.577537
6   feature_109           1018           64.964901
30  feature_578            949           60.561583
25  feature_345            794           50.670070
7   feature_112            715           45.628590
29  feature_562            273           17.421825
27  feature_546            260           16.592214

| Feature         | Action          |
| --------------- | --------------- |
| **feature_157** | Drop            |
| **feature_220** | Drop            |
| **feature_109** | Drop            |
| **feature_578** | Drop            |
| **feature_345** | Keep as flag    |
| **feature_112** | Keep as flag    |
| **feature_562** | Straight impute |
| **feature_546** | Straight impute |


---

> DROP
- Drop features that are MCAR or weak MAR/MNAR with no significant link to target

In [15]:
# Drop features based on analysis
features_to_drop_final = ['feature_157', 'feature_220', 'feature_109', 'feature_578']

# Before dropping
print("Data shape before final drop: ", data_reduced.shape)

# Drop the features
data_reduced_final = data_reduced.drop(columns=features_to_drop_final)
print("Data shape after final drop: ", data_reduced_final.shape)

# Look
data_reduced_final.head()

Data shape before final drop:  (1567, 85)
Data shape after final drop:  (1567, 81)


feature_0  feature_1  feature_10  feature_13  feature_100  feature_103  feature_112  feature_118  feature_121  feature_135  ...  feature_526  feature_527  feature_570  feature_571  feature_572  feature_573  feature_574  feature_575  feature_576  feature_577
0    3030.93    2564.00     -0.0034         0.0       0.0002      -0.0042          NaN       0.6002        15.88        123.0  ...       0.5064       6.6926     533.8500       2.1113         8.95       0.3157       3.0624       0.1026       1.6765      14.9509
1    3095.78    2465.14     -0.0148         0.0      -0.0004      -0.0045          NaN       0.5958        15.88         98.0  ...       0.8832       8.8370     535.0164       2.4335         5.92       0.2653       2.0111       0.0772       1.1065      10.9003
2    2932.61    2559.94      0.0013         0.0       0.0006      -0.0026       0.4684       0.6015        15.90         89.0  ...       0.6451       6.4568     535.0245       2.0293        11.21       0.1882       4.0923       0.0640       2.0952       9.2721
3    2988.72    2479.90     -0.0033         0.0      -0.0002      -0.0059       0.4647       0.6016        15.55        127.0  ...       0.7404       6.4865     530.5682       2.0253         9.33       0.1738       2.8971       0.0525       1.7585       8.5831
4    3032.24    2502.87     -0.0072         0.0       0.0004      -0.0045          NaN       0.5913        15.75        119.0  ...       2.2181       6.3745     532.0155       2.0275         8.83       0.2224       3.1776       0.0706       1.6597      10.9698

[5 rows x 81 columns]

---

> BINARY FLAGS
- Create binary flags for features with moderate missingness linked to target

In [16]:
# Create binary flags
for col in ['feature_345', 'feature_112']:
    flag_col = f"{col}_missing_flag"
    data_reduced_final[flag_col] = data_reduced_final[col].isnull().astype(int)
    print(f"Created missingness flag: {flag_col}")

# Look
print("Data Shape: ", data_reduced_final.shape)
data_reduced_final

Created missingness flag: feature_345_missing_flag
Created missingness flag: feature_112_missing_flag
Data Shape:  (1567, 83)


feature_0  feature_1  feature_10  feature_13  feature_100  feature_103  feature_112  feature_118  feature_121  feature_135  ...  feature_570  feature_571  feature_572  feature_573  feature_574  feature_575  feature_576  feature_577  feature_345_missing_flag  feature_112_missing_flag
0       3030.93    2564.00     -0.0034         0.0       0.0002      -0.0042          NaN       0.6002        15.88        123.0  ...     533.8500       2.1113         8.95       0.3157       3.0624       0.1026       1.6765      14.9509                         1                         1
1       3095.78    2465.14     -0.0148         0.0      -0.0004      -0.0045          NaN       0.5958        15.88         98.0  ...     535.0164       2.4335         5.92       0.2653       2.0111       0.0772       1.1065      10.9003                         1                         1
2       2932.61    2559.94      0.0013         0.0       0.0006      -0.0026       0.4684       0.6015        15.90         89.0  ...     535.0245       2.0293        11.21       0.1882       4.0923       0.0640       2.0952       9.2721                         0                         0
3       2988.72    2479.90     -0.0033         0.0      -0.0002      -0.0059       0.4647       0.6016        15.55        127.0  ...     530.5682       2.0253         9.33       0.1738       2.8971       0.0525       1.7585       8.5831                         0                         0
4       3032.24    2502.87     -0.0072         0.0       0.0004      -0.0045          NaN       0.5913        15.75        119.0  ...     532.0155       2.0275         8.83       0.2224       3.1776       0.0706       1.6597      10.9698                         1                         1
...         ...        ...         ...         ...          ...          ...          ...          ...          ...          ...  ...          ...          ...          ...          ...          ...          ...          ...          ...                       ...                       ...
1562    2899.41    2464.36     -0.0057         0.0       0.0000      -0.0094          NaN          NaN        15.69        212.0  ...     536.3418       2.0153         7.98       0.2363       2.6401       0.0785       1.4879      11.7256                         1                         1
1563    3052.31    2522.55     -0.0093         0.0      -0.0004      -0.0116          NaN          NaN        15.92         88.0  ...     537.9264       2.1814         5.48       0.3891       1.9077       0.1213       1.0187      17.8379                         0                         1
1564    2978.81    2379.78         NaN         NaN      -0.0001      -0.0142          NaN          NaN          NaN         85.0  ...     530.3709       2.3435         6.49       0.4154       2.1760       0.1352       1.2237      17.7267                         1                         1
1565    2894.92    2532.01      0.0032         0.0       0.0004      -0.0087          NaN          NaN        15.72        107.0  ...     534.3936       1.9098         9.13       0.3669       3.2524       0.1040       1.7085      19.2104                         1                         1
1566    2944.92    2450.76         NaN         NaN       0.0002      -0.0102          NaN          NaN          NaN        112.0  ...     528.7918       2.0831         6.81       0.4774       2.2727       0.1495       1.2878      22.9183                         1                         1

[1567 rows x 83 columns]

---

> IMPUTATION  
- For feature_562 and feature_546, we will impute the missing values
- Done after removing redundant and clearly non-informative features
- But before: outlier detection, feature engineering, and scaling.

Why not earlier? (before feature removal or missingness analysis):
- You might waste effort imputing columns that will later be dropped (e.g., correlated missingness).
- You lose the ability to test for MCAR/MAR/MNAR, because imputation hides the missingness pattern.
- Early imputation can bias your chi-square tests (since missing values are replaced, you can’t tell if they correlate with yield).

Why not later? (after outlier or feature engineering)
- Outlier detection relies on complete data; missing values cause algorithms like Isolation Forest or Z-score to fail.
- Feature engineering (e.g., mean, variance, PCA) also requires numeric completeness; missing values propagate NaNs.
- Temporal or rolling-window features would break since NaNs interrupt sequences.
- So postponing imputation blocks these next steps.

Why imputation before scaling
- Scaling (StandardScaler, RobustScaler) computes mean/median of features.
- If NaNs remain, these scalers cannot compute proper parameters.

Domain-specific reasoning (Manufacturing context)
- Missing values usually come from sensor read failures or equipment maintenance states.
- But once you’ve determined a feature is safe to impute (i.e., not missing-not-at-random due to yield),
it’s best to impute now to restore the dataset’s integrity before statistical modeling.
- Otherwise, downstream models (like PCA or yield classifiers) will interpret NaNs as data loss, not as a signal.

In [17]:
# Count missing values
missing_counts = data_reduced_final[['feature_562', 'feature_546']].isnull().sum()
print("Missing value counts:")
print(missing_counts)

Missing value counts:
feature_562    273
feature_546    260
dtype: int64


In [18]:
# Study on features that will be imputed
data_reduced_final[['feature_562', 'feature_546']].describe()

feature_562  feature_546
count  1294.000000  1307.000000
mean    262.729683     1.039630
std       7.630585     0.389066
min     242.286000     0.444400
25%     259.972500     0.797500
50%     264.272000     0.911100
75%     265.707000     1.285550
max     311.404000     3.978600

| Statistic | feature_562                | feature_546                  |
| --------- | -------------------------- | ---------------------------- |
| Count     | 1294 / 1567 (~17% missing) | 1307 / 1567 (~16.6% missing) |
| Mean      | 262.7                      | 1.04                         |
| Std       | 7.63                       | 0.39                         |
| Range     | 242.3 – 311.4              | 0.44 – 3.98                  |

These look like continuous sensor signals, possibly temperature, current, or pressure readings.

✅ Both are numerical, continuous features.  
So we’ll treat them using continuous-variable imputation strategies, not categorical ones.

In [19]:
# Before imputing anything, we use plotly to visualize the distributions
fig = make_subplots(rows=1, cols=2, subplot_titles=('feature_562 Distribution', 'feature_546 Distribution'))
fig.add_trace(
    go.Histogram(
        x=data_reduced_final['feature_562'],
        nbinsx=100,
        marker_color='indianred',
        opacity=0.7,
        name='feature_562',
        hovertemplate='Value: <b>%{x:.2f}</b><br>Count: %{y}<extra></extra>'
    ),
    row=1, col=1
)
fig.add_trace(
    go.Histogram(
        x=data_reduced_final['feature_546'],
        nbinsx=100,
        marker_color='royalblue',
        opacity=0.7,
        name='feature_546',
        hovertemplate='Value: <b>%{x:.2f}</b><br>Count: %{y}<extra></extra>'
    ),
    row=1, col=2
)
fig.update_layout(title_text='Distributions of feature_562 and feature_546')
fig.show()

In [20]:
# Value frequency inspection
for col in ['feature_562', 'feature_546']:
    print(f"Top 5 value counts for {col}:")
    print(data_reduced_final[col].value_counts(dropna=True).head())
    print()

Top 5 value counts for feature_562:
feature_562
264.272    396
249.176      2
264.188      2
262.482      2
267.064      2
Name: count, dtype: int64

Top 5 value counts for feature_546:
feature_546
0.8273    142
0.8035     48
0.8217     27
0.8482      9
1.1996      2
Name: count, dtype: int64



#### > Value Frequency Interpretation (Before Imputation)

| Feature         | Dominant Value | Count                  | % of Total             | Next Highest Count | Distribution Pattern                      |
| --------------- | -------------- | ---------------------- | ---------------------- | ------------------ | ----------------------------------------- |
| **feature_562** | 264.272        | 396 / 1567 ≈ **25.3%** | Clear dominant plateau | 2 counts for next  | *Highly discrete-like with a single mode* |
| **feature_546** | 0.8273         | 142 / 1567 ≈ **9.1%**  | Noticeable mode        | 48, 27, 9, 2       | *Semi-discrete with gentle mode + tail*   |

So roughly:
- feature_562 behaves almost like a sensor with calibration plateau — it stays fixed near 264.272 for many wafers.
- feature_546 shows a clustered distribution near 0.8 but with more spread.

#### > Manufacturing Interpretation  

🔹 feature_562 (~264.27 constant)
- The machine sensor measures a steady-state or reference output (e.g., voltage at a controlled process stage).
- 264.27 could represent a “nominal” reading under normal operation.
- Missing values may occur during unstable or non-measured stages (e.g., machine idle, reset).
- So, missing ≠ random; it’s possibly MNAR (Missing Not At Random) — related to machine state.

🔹 feature_546 (~0.82 cluster)
- It's an operational ratio (maybe normalized signal, or gas/flow ratio).

#### > Hence, KNN imputation is the most appropriate at this stage.

| Advantage                     | Explanation                                                                                                              |
| ----------------------------- | ------------------------------------------------------------------------------------------------------------------------ |
| **Local Context–Driven**        | KNN Imputer doesn’t look at the global distribution (so it doesn’t see or get biased by that spike). This way, the spike will naturally remain, but not be artificially inflated. |
| **Non-parametric**            | Doesn’t assume normality; ideal for sensor readings with skew.                                                           |
| **Inter-feature correlation** | Uses the structure of the dataset (other sensors) to infer realistic replacements.                                       |
| **Anomaly sensitivity**       | Retains outlier patterns; doesn’t over-smooth like mean/median imputation.                                               |


#### > Again, Objective Context

- Not trying to build a generative model or visualize patterns — your goal is to detect anomalies and predict pass/fail (yield).
- Means the downstream models (like Isolation Forest, Random Forest, XGBoost, etc.) will learn patterns in multivariate feature space.

#### > How KNN Imputation affects the downstream model (and how much tuning matters)

(1) When it matters:
- Missingness rate is high (> 10–15% of total entries).
- Have correlated sensor readings (which SECOM does — sensors can drift together).
- Going to use distance-based algorithms (e.g., KNN, Isolation Forest, LOF, etc.) that are sensitive to small value shifts.

Because in those cases:
- The choice of neighbors (n_neighbors),
- and the distance weighting  
can slightly shift the imputed values and thus the cluster structure.

That can lead to slightly different anomaly scores or decision boundaries.  



(2) When it doesn’t matter much:
- Already dropped features with high missingness,
- Remaining missingness is low (< 5–10%),
- Are training tree-based models (like RandomForest, XGBoost, LightGBM),  
then, small differences in KNN imputation make almost no difference.
Tree-based models are robust to small value shifts because they split based on thresholds, not exact distances.

So tuning n_neighbors=3, 5, or 7 won’t change much beyond noise.

In [21]:
# Quick test of imputation methods with different neighbors
from sklearn.impute import KNNImputer

# Features to test
cols = ['feature_562', 'feature_546']

# Dictionary to store imputed data
imputed_dict = {}

# Test different neighbor values
for k in [3, 5, 7]:
    imputer = KNNImputer(n_neighbors=k, weights='distance')
    imputed_df = pd.DataFrame(imputer.fit_transform(data_reduced_final[cols]), columns=cols)
    imputed_dict[k] = imputed_df

# Inspect basic stats
for k, df in imputed_dict.items():
    print(f"--- K={k} ---")
    print(df.describe())
    print()


# Plot distributions for different k values
colors = {3: 'crimson', 5: 'limegreen', 7: 'dodgerblue'}

for col in cols:
    fig = go.Figure()
    
    for k, df in imputed_dict.items():
        fig.add_trace(go.Histogram(
            x=df[col],
            nbinsx=100,
            name=f'K={k}',
            opacity=0.2,
            marker_color=colors[k],
            hovertemplate='Value: %{x:.2f}<br>Count: %{y}<extra></extra>'
        ))
    
    fig.update_layout(
        title=f'KNN Imputation Sensitivity for {col}',
        barmode='overlay',
        xaxis_title='Value',
        yaxis_title='Count',
        template='plotly_white',
        height=600,
        width=900
    )
    
    fig.show()

--- K=3 ---
       feature_562  feature_546
count  1567.000000  1567.000000
mean    262.603651     1.034742
std       7.169719     0.363953
min     242.286000     0.444400
25%     260.134409     0.803500
50%     264.272000     0.956000
75%     265.304000     1.242750
max     311.404000     3.978600

--- K=5 ---
       feature_562  feature_546
count  1567.000000  1567.000000
mean    262.634962     1.034127
std       7.126729     0.362312
min     242.286000     0.444400
25%     260.447000     0.803500
50%     264.272000     0.956400
75%     265.209000     1.237100
max     311.404000     3.978600

--- K=7 ---
       feature_562  feature_546
count  1567.000000  1567.000000
mean    262.654354     1.035844
std       7.104998     0.361257
min     242.286000     0.444400
25%     260.518000     0.803500
50%     264.272000     0.962900
75%     265.180000     1.235900
max     311.404000     3.978600



#### > What to look for when comparing K=3,5,7 imputation results:

1. Distribution shape:
- Compare histograms across K=3,5,7.
- If the spikes and tails are roughly in the same position, your imputation is stable.
A: Yes, same position

2. Descriptive stats:
- Compare mean, median, std in the printed describe() output.
- Small differences are fine; large shifts would indicate sensitivity.
Decision:
A: Yes, almost similar

3. If differences are negligible → stick with K=5.
- If differences affect spike heights or variance significantly → may consider adjusting K or using neighbor weighting differently.
A: No significant differences observed

In [22]:
# Normal imputation process
cols = ['feature_562', 'feature_546']
numeric_cols = data_reduced_final.select_dtypes(include='number').columns

# Check missing value ratio before imputation
missing_before = data_reduced_final[cols].isna().mean() * 100

# Apply KNN imputer
imputer = KNNImputer(n_neighbors=5, weights="distance")
## n_neighbors=5: balances local representativeness with computational efficiency.
## weights="distance": closer points have more influence (better for continuous sensors).

# Fit and transform
df_imputed = pd.DataFrame(imputer.fit_transform(data_reduced_final[numeric_cols]), columns=numeric_cols)
# Check missing value ratio after imputation
missing_after = df_imputed.isna().mean() * 100

# Combine for comparison
missing_compare = pd.DataFrame({
    'Before Imputation': missing_before,
    'After Imputation': missing_after
}).reset_index().rename(columns={'index': 'Feature'})

# Plotly comparison chart on plotly regarding the distribution before and after imputation
fig = make_subplots(rows=1, cols=2, subplot_titles=('feature_562 Distribution', 'feature_546 Distribution'))
fig.add_trace(
    go.Histogram(
        x=data_reduced_final['feature_562'],
        nbinsx=100,
        marker_color='indianred',
        opacity=0.5,
        name='Before Imputation',
        hovertemplate='Value: <b>%{x:.2f}</b><br>Count: %{y}<extra></extra>'
    ),
    row=1, col=1
)
fig.add_trace(
    go.Histogram(
        x=df_imputed['feature_562'],
        nbinsx=100,
        marker_color='darkred',
        opacity=0.5,
        name='After Imputation',
        hovertemplate='Value: <b>%{x:.2f}</b><br>Count: %{y}<extra></extra>'
    ),
    row=1, col=1
)

fig.add_trace(
    go.Histogram(
        x=data_reduced_final['feature_546'],
        nbinsx=100,
        marker_color='royalblue',
        opacity=0.5,
        name='Before Imputation',
        hovertemplate='Value: <b>%{x:.2f}</b><br>Count: %{y}<extra></extra>'
    ),
    row=1, col=2
)

fig.add_trace(
    go.Histogram(
        x=df_imputed['feature_546'],
        nbinsx=100,
        marker_color='darkblue',
        opacity=0.5,
        name='After Imputation',
        hovertemplate='Value: <b>%{x:.2f}</b><br>Count: %{y}<extra></extra>'
    ),
    row=1, col=2
)

fig.update_layout(
    barmode='overlay',
    title='Feature Distributions Before and After KNN Imputation',
    xaxis_title='Value',
    yaxis_title='Count',
    template='plotly_white',
    showlegend=True,
    height=600,
    width=900
)

fig.show()

In [23]:
# Making sure the missing values are imputed
print("Missing values in feature_562 and feature_546 after imputation:")
print(df_imputed.isnull().sum().sum())

# Combine imputed features back to the main dataframe
data_imputed = data_reduced_final.copy()
data_imputed[['feature_562', 'feature_546']] = df_imputed[['feature_562', 'feature_546']]

# Look at the final data shape
print("\nFinal data shape after imputation: ", data_imputed.shape)
data_imputed

Missing values in feature_562 and feature_546 after imputation:
0

Final data shape after imputation:  (1567, 83)


feature_0  feature_1  feature_10  feature_13  feature_100  feature_103  feature_112  feature_118  feature_121  feature_135  ...  feature_570  feature_571  feature_572  feature_573  feature_574  feature_575  feature_576  feature_577  feature_345_missing_flag  feature_112_missing_flag
0       3030.93    2564.00     -0.0034         0.0       0.0002      -0.0042          NaN       0.6002        15.88        123.0  ...     533.8500       2.1113         8.95       0.3157       3.0624       0.1026       1.6765      14.9509                         1                         1
1       3095.78    2465.14     -0.0148         0.0      -0.0004      -0.0045          NaN       0.5958        15.88         98.0  ...     535.0164       2.4335         5.92       0.2653       2.0111       0.0772       1.1065      10.9003                         1                         1
2       2932.61    2559.94      0.0013         0.0       0.0006      -0.0026       0.4684       0.6015        15.90         89.0  ...     535.0245       2.0293        11.21       0.1882       4.0923       0.0640       2.0952       9.2721                         0                         0
3       2988.72    2479.90     -0.0033         0.0      -0.0002      -0.0059       0.4647       0.6016        15.55        127.0  ...     530.5682       2.0253         9.33       0.1738       2.8971       0.0525       1.7585       8.5831                         0                         0
4       3032.24    2502.87     -0.0072         0.0       0.0004      -0.0045          NaN       0.5913        15.75        119.0  ...     532.0155       2.0275         8.83       0.2224       3.1776       0.0706       1.6597      10.9698                         1                         1
...         ...        ...         ...         ...          ...          ...          ...          ...          ...          ...  ...          ...          ...          ...          ...          ...          ...          ...          ...                       ...                       ...
1562    2899.41    2464.36     -0.0057         0.0       0.0000      -0.0094          NaN          NaN        15.69        212.0  ...     536.3418       2.0153         7.98       0.2363       2.6401       0.0785       1.4879      11.7256                         1                         1
1563    3052.31    2522.55     -0.0093         0.0      -0.0004      -0.0116          NaN          NaN        15.92         88.0  ...     537.9264       2.1814         5.48       0.3891       1.9077       0.1213       1.0187      17.8379                         0                         1
1564    2978.81    2379.78         NaN         NaN      -0.0001      -0.0142          NaN          NaN          NaN         85.0  ...     530.3709       2.3435         6.49       0.4154       2.1760       0.1352       1.2237      17.7267                         1                         1
1565    2894.92    2532.01      0.0032         0.0       0.0004      -0.0087          NaN          NaN        15.72        107.0  ...     534.3936       1.9098         9.13       0.3669       3.2524       0.1040       1.7085      19.2104                         1                         1
1566    2944.92    2450.76         NaN         NaN       0.0002      -0.0102          NaN          NaN          NaN        112.0  ...     528.7918       2.0831         6.81       0.4774       2.2727       0.1495       1.2878      22.9183                         1                         1

[1567 rows x 83 columns]

#### > Check on the charts

1. Preservation of the distribution
- Goal: Imputation should not distort the overall shape of the feature’s distribution.
- Reflection:
- For feature_562: Spike at 264.272 should still be dominant; other smaller peaks/values roughly preserved.
- For feature_546: Clusters (like 0.82, 1.17) remain visible; KNN just increases the counts slightly where missing values fit naturally.
- Interpretation: KNN is preserving the natural sensor behavior — good sign for anomaly detection.

2. Filling of missing values
- Goal: All missing values are replaced.
- Reflection: After imputation, no NaNs remain (missing_after = 0).
- Interpretation: Dataset is ready for modeling; no need to worry about missing-value errors.

3. Spike growth
- Goal: Understand that some spikes (like 1.17 for feature_546) grow because missing values are pulled toward clusters.
- Reflection: Not a problem — this is normal KNN behavior.
- Interpretation: Shows that imputation aligns with local sensor correlations, which preserves physical meaning.

---

### 2.3 Constant Columns and Duplicates Columns
> Check and handle

In [24]:
# Display summary table
print(data_imputed.describe())

# Get features that is exact duplicates
duplicate_features = []
seen = set()
for col in data_imputed.columns:
    col_tuple = tuple(data_imputed[col])
    if col_tuple in seen:
        duplicate_features.append(col)
    else:
        seen.add(col_tuple)
print(f"Duplicate features found: {duplicate_features}")
data_imputed_dup = data_imputed.drop(columns=duplicate_features)
print("Data shape after dropping duplicate columns: ", data_imputed_dup.shape)
print("")

# Drop constant columns (std dev = 0)
constant_features = [col for col in data_imputed_dup.columns if data_imputed_dup[col].nunique() == 1]
for col in constant_features:
    print(f"Constant feature found: {col} with value {data_imputed_dup[col].iloc[0]}")
data_imputed_const = data_imputed_dup.drop(columns=constant_features)
print("Data shape after dropping constant columns: ", data_imputed_const.shape)

         feature_0    feature_1   feature_10  feature_13  feature_100  feature_103  feature_112  feature_118  feature_121  feature_135  ...  feature_570  feature_571  feature_572  feature_573  feature_574  feature_575  feature_576  feature_577  feature_345_missing_flag  feature_112_missing_flag
count  1561.000000  1560.000000  1565.000000      1564.0  1561.000000  1565.000000   852.000000  1543.000000  1558.000000  1562.000000  ...  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000               1567.000000               1567.000000
mean   3014.452896  2495.850231     0.000146         0.0    -0.000021    -0.009789     0.457538     0.598412    15.796425   117.960948  ...   530.523623     2.101836    28.450165     0.345636     9.162315     0.104729     5.563747    16.642363                  0.506701                  0.456286
std      73.621787    80.407705     0.009302         0.0     0.000356     0.003065     0.048939     0.008102    

---

## 3. Outlier Detection & Treatment

- When: Right after missing value imputation, before feature engineering.
- Why: Outliers can skew derived statistics (mean, std, etc.) used in later steps.

In semiconductor manufacturing:
- Outliers may represent real anomalies (bad wafers) or sensor spikes.
- Instead of removing all, label them first (for anomaly analysis).

Steps:
- Use robust scaling (Median/IQR) to spot them.
- Use Isolation Forest / Z-score threshold to mark them.
- Create a column like outlier_flag (don’t remove yet).
- Optionally: Keep two datasets:  
-- df_clean (winsorized / capped)  
-- df_with_outliers (for anomaly detection model)

Why check for outliers before normalization?
- Because outliers can distort the scaling, especially with methods like MinMaxScaler. Consider using RobustScaler or log transformation if outliers are significant.

In [7]:
# Analyze data distributions for complete features
complete_features = missing_summary[missing_summary['Missing_Percentage'] == 0]['Feature'].tolist()
print(f"Number of complete features (0% missing): {len(complete_features)}")

if len(complete_features) > 0:
    # Statistical summary for complete features
    complete_data = data[complete_features]
    print(f"\nStatistical summary for complete features:")
    print(complete_data.describe())
    
    # Check for outliers using IQR method
    Q1 = complete_data.quantile(0.25)
    Q3 = complete_data.quantile(0.75)
    IQR = Q3 - Q1
    outlier_mask = ((complete_data < (Q1 - 1.5 * IQR)) | (complete_data > (Q3 + 1.5 * IQR))).any(axis=1)
    print(f"\nNumber of samples with outliers: {outlier_mask.sum()}")
    print(f"Percentage of samples with outliers: {outlier_mask.mean() * 100:.2f}%")
    ## Why use mean here? It is the same as:
    # If 1000 samples and 243 of them have at least one outlier:
    # outlier_mask.mean() = 1 + 1 + 1 ... (243 times) + 0 + 0 + ... (757 times) / 1000 = 0.243 ## Due to True values being 1, False being 0
    # outlier_mask.sum() = 243 
    # outlier_mask.mean() * 100 = 24.3%
else:
    print("No complete features found for statistical analysis")


Number of complete features (0% missing): 52

Statistical summary for complete features:
        feature_20  feature_571  feature_570  feature_573  feature_393  feature_429  feature_390  feature_392  feature_577  feature_574  ...  feature_114  feature_113  feature_527  feature_526  feature_524  feature_523  feature_522  feature_521  feature_520  feature_120
count  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  ...  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000  1567.000000
mean      1.405054     2.101836   530.523623     0.345636     0.133990     4.171844     1.431868     0.004533    16.642363     9.162315  ...     0.000123     0.945424     6.395717     1.443457     5.687782     0.453896    14.728866    11.610080     2.695999     6.310863
std       0.016737     0.275112    17.499736     0.248478     0.038408     6.435390    20.326415  

In [9]:
# Visualize distributions for a sample of features
if len(complete_features) > 0:
    # Select up to 16 features for visualization
    sample_features = complete_features[:16] if len(complete_features) >= 16 else complete_features

    # Create a 4x4 grid of subplots
    fig = make_subplots(
        rows=4,
        cols=4,
        subplot_titles=sample_features,
        horizontal_spacing=0.08,
        vertical_spacing=0.10
    )
    
    for i, feature in enumerate(sample_features):
        row = i // 4 + 1
        col = i % 4 + 1
        
        # Add histogram for each feature
        fig.add_trace(
            go.Histogram(
                x=data[feature].dropna(),
                nbinsx=30,
                marker=dict(color='lightblue', line=dict(color='black', width=1)),
                opacity=0.75,
                name=feature
            ),
            row=row, col=col
        )
        
        # Set axis labels for each subplot
        fig.update_xaxes(title_text="Value", row=row, col=col)
        fig.update_yaxes(title_text="Frequency", row=row, col=col)
    
    # Update overall layout
    fig.update_layout(
        title_text="Distribution of Complete Features (Interactive)",
        showlegend=False,
        height=900,
        width=1400,
        title_x=0.5,
        template='plotly_white'
    )
    
    # Optional: light grid lines for clarity
    fig.update_xaxes(showgrid=True, gridwidth=0.5, gridcolor='lightgray')
    fig.update_yaxes(showgrid=True, gridwidth=0.5, gridcolor='lightgray')

    fig.show()

else:
    print("No complete features available for distribution visualization")


| **Pattern**                                        | **What It Means (in SECOM context)**                                                                               | **Potential Action / Usefulness**                                                                |
| -------------------------------------------------- | ------------------------------------------------------------------------------------------------------------------ | ------------------------------------------------------------------------------------------------ |
| **Normal (bell-shaped)**                           | Sensor readings cluster around a mean value, symmetric distribution.                                               | Likely stable and well-calibrated sensor. Baseline process behavior.                             |
| **Right-skewed (long tail to the right)**          | Most readings are low, few high spikes. Could indicate occasional high sensor readings (e.g., temperature spikes). | Investigate what causes spikes. Check if spikes correspond to defective samples.                 |
| **Left-skewed (long tail to the left)**            | Most readings are high, few low outliers.                                                                          | Could suggest low outliers (dropouts, low voltage, etc.). Check correlation with quality issues. |
| **Bimodal / Multimodal (two or more peaks)**       | Sensor shows two different operating regimes (e.g., two production lines, machines, shifts, or process modes).                       | Could mean process inconsistency. Important to model separately or add categorical indicator.    |
| **Flat / Uniform**                                 | Values spread roughly evenly across range.                                                                         | Feature might not have a strong relationship with output; could be noise.                        |
| **Very narrow spike (little variance)**            | All readings nearly identical.                                                                                     | Low variance → feature may be redundant or useless for modeling (drop it).                       |
| **Outliers (isolated bins far from main cluster)** | Unusual readings far from majority.                                                                                | Possible sensor faults, measurement errors, or rare events worth investigating.                  |


In [10]:
# Analyze data distributions for all features and focus on outliers impacting yield
# > Step 1: For each feature, compare the failure rate among outlier samples vs non-outlier samples.
# If fail rate is significantly higher (or lower) in outliers, then outliers carry signal and should be treated carefully.
# If fail rates are similar, outliers are likely noise/neutral — safe to cap or transform.

Q1 = data_features.quantile(0.25)
Q3 = data_features.quantile(0.75)
IQR = Q3 - Q1

outliers_df = (data_features < (Q1 - 1.5 * IQR)) | (data_features > (Q3 + 1.5 * IQR))

comparison_results = []

for feature in data_features.columns:
    outlier_mask = outliers_df[feature]
    
    if outlier_mask.sum() == 0:
        # No outliers for this feature, skip or mark as neutral
        continue
    
    # Fail rate among outliers
    fail_rate_outliers = data.loc[outlier_mask, 'target'].eq(1).mean()
    # Fail rate among non-outliers
    fail_rate_non_outliers = data.loc[~outlier_mask, 'target'].eq(1).mean()
    
    comparison_results.append({
        'Feature': feature,
        'Fail_Rate_Outliers': fail_rate_outliers,
        'Fail_Rate_Non_Outliers': fail_rate_non_outliers,
        'Outlier_Count': outlier_mask.sum(),
        'Non_Outlier_Count': (~outlier_mask).sum(),
        'Fail_Rate_Difference': fail_rate_outliers - fail_rate_non_outliers
    })

comparison_df = pd.DataFrame(comparison_results)
comparison_df = comparison_df.sort_values(by='Fail_Rate_Difference', ascending=False)

print("Outlier Impact on Failure Rates by Feature:")
print(comparison_df.head(100))

# However we try to take into account the Outlier_Count as well when interpreting the results:
# We want those with high Outlier_Count and high Fail_Rate_Difference to be more reliable indicators.
high_outlier_count_threshold = data.shape[0] * 0.05  # e.g., at least 5% of samples are outliers
print("\nFeatures with High Outlier Count and Significant Fail Rate Difference:")
reliable_indicators = comparison_df[
    (comparison_df['Outlier_Count'] >= high_outlier_count_threshold) &
    (comparison_df['Fail_Rate_Difference'] >= 0.05)  # e.g., at least 5% difference
]
print(f"Number of reliable indicators found: {len(reliable_indicators)}")
print(reliable_indicators.head(20))

# > Step 2: Interpretation
# Fail_Rate_Difference >> 0: outliers are enriched for failures → do not neutralize, they carry predictive info.
# Fail_Rate_Difference ≈ 0: outliers have no impact on fail rate → can consider neutralizing (e.g., clipping or winsorizing).
# Fail_Rate_Difference < 0: outliers might even have lower fail rate → maybe worth investigating further.


## <To Study> 
## Extract the correlations between features that have high outlier fail rate differences
## to see if they cluster into groups indicating specific failure modes

Outlier Impact on Failure Rates by Feature:
         Feature  Fail_Rate_Outliers  Fail_Rate_Non_Outliers  Outlier_Count  Non_Outlier_Count  Fail_Rate_Difference
48    feature_55            0.400000                0.065301              5               1562              0.334699
423  feature_561            0.333333                0.064827              9               1558              0.268507
57    feature_64            0.287879                0.056629             66               1501              0.231250
386  feature_493            0.285714                0.065385              7               1560              0.220330
198  feature_221            0.285714                0.065385              7               1560              0.220330
..           ...                 ...                     ...            ...                ...                   ...
15    feature_17            0.125000                0.065764             16               1551              0.059236
62    feature_70    

| Scenario                                             | Action or Interpretation                                                                                                                                 |
| ---------------------------------------------------- | -------------------------------------------------------------------------------------------------------------------------------------------------------- |
| **Low Outlier_Count + Very High Fail_Rate_Outliers** | Strong potential signal, but be cautious. Consider verifying with more data or cross-validation. Keep the feature but treat it as less reliable. |
| **High Outlier_Count + High Fail_Rate_Outliers**     | Strong and statistically more reliable signal. Definitely useful for modeling.                                                                           |
| **Low Outlier_Count + Low Fail_Rate_Outliers**       | Probably noise or irrelevant outliers, can ignore.                                                                                                       |
| **High Outlier_Count + Low Fail_Rate_Outliers**      | Outliers not informative for failure; can ignore or treat as normal.                                                                                     |


In [11]:
top_features = comparison_df.head(30) # top 30 features where outliers differ most in fail rate

fig = go.Figure()

fig.add_trace(go.Bar(
    x=top_features['Feature'],
    y=top_features['Fail_Rate_Outliers'],
    name='Fail Rate (Outliers)',
    marker_color='crimson',
    hovertemplate='Feature: %{x}<br>Fail Rate (Outliers): %{y:.2%}<extra></extra>'
))

fig.add_trace(go.Bar(
    x=top_features['Feature'],
    y=top_features['Fail_Rate_Non_Outliers'],
    name='Fail Rate (Non-Outliers)',
    marker_color='steelblue',
    hovertemplate='Feature: %{x}<br>Fail Rate (Non-Outliers): %{y:.2%}<extra></extra>'
))

fig.update_layout(
    title='Fail Rate Comparison: Outliers vs Non-Outliers (Top 30 Features)',
    xaxis_title='Feature',
    yaxis_title='Fail Rate',
    barmode='group',
    yaxis=dict(range=[0, 1]),
    template='plotly_white',
    height=500
)

fig.show()

## 4. Temporal Analysis - Process Drift Detection

Why this matters: Micron's smart manufacturing deals with process variation over time. This shows how to detect drift/jumps in sensor data over production time.

In [12]:
test_col = 6
print("Analyzing sensor drift patterns...")

if 'data_timestamp' in globals() or 'data_timestamp' in locals():
    ts = pd.to_datetime(data_timestamp)
    if len(ts) != len(data):
        print("Warning: timestamp length does not match data length — skipping temporal analysis.")
    else:
        if isinstance(complete_features, list) and len(complete_features) > 0:
            df_complete = data[complete_features].copy()
        else:
            raise ValueError("complete_features must be a non-empty list of column names")

        # concat the feature DataFrame with the timestamp Series
        df_ts = pd.concat([df_complete.reset_index(drop=True), ts.reset_index(drop=True).rename('timestamp')], axis=1)
        print(f"Number of rows in concatenated DataFrame: {df_ts.shape[0]}, columns: {df_ts.shape[1]}")

        # set timestamp index for time-based analysis
        df_ts['timestamp'] = pd.to_datetime(df_ts['timestamp'])
        df_ts = df_ts.set_index('timestamp').sort_index()

        # proceed with plotting / drift detection using df_ts
        sample_sensors = complete_features[:test_col] if len(complete_features) >= test_col else complete_features
        if len(sample_sensors) == 0:
            print("No complete features available for temporal analysis.")
        else:
            window = 50            # rolling window for trend estimation
            min_periods = 10       # minimum periods to compute rolling stats
            sigma_threshold = 3.0  # number of std deviations to call a jump

            jump_summary = []
            rows = int(np.ceil(len(sample_sensors) / 2))
            cols = 2 if len(sample_sensors) > 1 else 1

            # compute rolling stats and detect jumps
            for sensor in sample_sensors:
                series = df_ts[sensor].astype(float)
                rolling_mean = series.rolling(window=window, min_periods=min_periods).mean()
                rolling_std = series.rolling(window=window, min_periods=min_periods).std()
                jumps_mask = (series - rolling_mean).abs() > (sigma_threshold * rolling_std)
                jumps_mask = jumps_mask.fillna(False)
                total_jumps = int(jumps_mask.sum())
                pct_jumps = jumps_mask.mean() * 100 if len(jumps_mask) > 0 else 0.0

                jump_summary.append({
                    'sensor': sensor,
                    'jump_count': total_jumps,
                    'jump_pct': pct_jumps,
                    'rolling_window': window,
                    'sigma_threshold': sigma_threshold
                })

                print(f"{sensor}: {total_jumps} jumps detected ({pct_jumps:.2f}%) with window={window}, sigma={sigma_threshold}")

            jump_summary_df = pd.DataFrame(jump_summary).sort_values('jump_count', ascending=False)
            print("\nJump summary (top sensors):")
            display(jump_summary_df.head(20))

            # Plot: try Plotly first, fallback to Matplotlib if Plotly internals raise ModuleNotFoundError
            try:
                fig = make_subplots(rows=rows, cols=cols, subplot_titles=sample_sensors)
                for i, sensor in enumerate(sample_sensors):
                    series = df_ts[sensor].astype(float)
                    rolling_mean = series.rolling(window=window, min_periods=min_periods).mean()
                    rolling_std = series.rolling(window=window, min_periods=min_periods).std()
                    jumps_mask = (series - rolling_mean).abs() > (sigma_threshold * rolling_std)
                    jumps_mask = jumps_mask.fillna(False)
                    jump_times = series.index[jumps_mask]
                    jump_vals = series.loc[jump_times]

                    row = i // cols + 1
                    col = i % cols + 1

                    # basic traces (avoid complex 'line' validators where possible)
                    fig.add_trace(go.Scatter(x=series.index, y=series.values, mode='lines', name=f'{sensor} raw'), row=row, col=col)
                    fig.add_trace(go.Scatter(x=rolling_mean.index, y=rolling_mean.values, mode='lines', name=f'{sensor} rolling_mean',
                                             line=dict(dash='dash', width=2)), row=row, col=col)

                    if not jump_times.empty:
                        fig.add_trace(go.Scatter(x=jump_times, y=jump_vals.values, mode='markers',
                                                 marker=dict(color='red', size=6), name=f'{sensor} jumps'), row=row, col=col)

                fig.update_layout(title="Sensor Drift & Jump Markers (rolling mean/std)", height=300 * rows, template='plotly_white', showlegend=False)
                fig.show()

            except ModuleNotFoundError as e:
                # Fallback: Matplotlib static plots
                print(f"Plotly internals failed ({e}). Falling back to Matplotlib plotting.")
                import matplotlib.dates as mdates
                fig, axes = plt.subplots(rows, cols, figsize=(12 * cols, 3 * rows), squeeze=False)
                for i, sensor in enumerate(sample_sensors):
                    series = df_ts[sensor].astype(float)
                    rolling_mean = series.rolling(window=window, min_periods=min_periods).mean()
                    rolling_std = series.rolling(window=window, min_periods=min_periods).std()
                    jumps_mask = (series - rolling_mean).abs() > (sigma_threshold * rolling_std)
                    jumps_mask = jumps_mask.fillna(False)
                    jump_times = series.index[jumps_mask]
                    jump_vals = series.loc[jump_times]

                    r = i // cols
                    c = i % cols
                    ax = axes[r][c]
                    ax.plot(series.index, series.values, color='steelblue', linewidth=0.8)
                    ax.plot(rolling_mean.index, rolling_mean.values, color='orange', linestyle='--', linewidth=1.4)
                    if not jump_times.empty:
                        ax.scatter(jump_times, jump_vals.values, color='red', s=20, zorder=5)
                    ax.set_title(sensor)
                    ax.xaxis.set_major_formatter(mdates.AutoDateFormatter(mdates.AutoDateLocator()))
                    ax.grid(True, alpha=0.3)
                plt.tight_layout()
                plt.show()
else:
    print("No timestamp available (data_timestamp not set). Skipping temporal analysis.")

Analyzing sensor drift patterns...
Number of rows in concatenated DataFrame: 1567, columns: 53
feature_20: 14 jumps detected (0.89%) with window=50, sigma=3.0
feature_571: 18 jumps detected (1.15%) with window=50, sigma=3.0
feature_570: 49 jumps detected (3.13%) with window=50, sigma=3.0
feature_573: 53 jumps detected (3.38%) with window=50, sigma=3.0
feature_393: 7 jumps detected (0.45%) with window=50, sigma=3.0
feature_429: 24 jumps detected (1.53%) with window=50, sigma=3.0

Jump summary (top sensors):


sensor  jump_count  jump_pct  rolling_window  sigma_threshold
3  feature_573          53  3.382259              50              3.0
2  feature_570          49  3.126994              50              3.0
5  feature_429          24  1.531589              50              3.0
1  feature_571          18  1.148692              50              3.0
0   feature_20          14  0.893427              50              3.0
4  feature_393           7  0.446713              50              3.0

## 4. Data Preprocessing

Now we'll clean and preprocess the data for machine learning. This includes:
- Handling missing values using appropriate imputation strategies
- Feature scaling and normalization
- Outlier treatment
- Saving the cleaned dataset


In [13]:
# Preprocess the data using our utility function
print("Starting data preprocessing...")
print("This may take a few minutes due to the large dataset size...")

# Use KNN imputation for missing values (most sophisticated approach)
processed_data = preprocess_data(data, method='knn')

print(f"\nPreprocessing completed!")
print(f"Original shape: {data.shape}")
print(f"Processed shape: {processed_data.shape}")
print(f"Missing values after preprocessing: {processed_data.isnull().sum().sum()}")


Starting data preprocessing...
This may take a few minutes due to the large dataset size...

= Preprocessing data using 'knn' imputation...
> Missing values before imputation (per feature):
feature_0       6
feature_1       7
feature_2      14
feature_3      14
feature_4      14
               ..
feature_585     1
feature_586     1
feature_587     1
feature_588     1
feature_589     1
Length: 590, dtype: int64
> Missing values before imputation (total): 41951/924530 (4.54%)
> Missing values after imputation (total): 0/924530 (0.00%)
> Preprocessed data saved to data/processed/secom_preprocessed_data.csv
> Shape: (1567, 591)
> Missing values: 0

Preprocessing completed!
Original shape: (1567, 591)
Processed shape: (1567, 591)
Missing values after preprocessing: 0


In [14]:
# Verify the preprocessing results
print("Verifying preprocessing results...")

# Check for any remaining missing values
remaining_missing = processed_data.isnull().sum().sum()
print(f"Remaining missing values: {remaining_missing}")

# Check target distribution (if available)
if 'target' in processed_data.columns:
    print(f"\nTarget distribution after preprocessing:")
    print(processed_data['target'].value_counts())
    print(f"Class balance: {processed_data['target'].value_counts().min() / processed_data['target'].value_counts().max():.3f}")

# Display sample of processed data
print(f"\nSample of processed data:")
processed_data.head()

# Save the processed data for future modeling steps
processed_data.to_csv('data/processed/secom_preprocessed_data.csv', index=False)
print("Processed data saved to 'data/processed/secom_preprocessed_data.csv'")


Verifying preprocessing results...
Remaining missing values: 0

Target distribution after preprocessing:
target
-1    1463
 1     104
Name: count, dtype: int64
Class balance: 0.071

Sample of processed data:
Processed data saved to 'data/processed/secom_preprocessed_data.csv'


#### Class Imbalance Strategy - DEAL in 03_ml_yield_prediction.ipynb

Why this matter: The SECOM dataset has a significant class imbalance (more passing wafers than failing ones). Addressing this is crucial for building effective predictive models that can accurately identify failing wafers.


> Must choose objective (catch most fails = high recall, or limit false alarms = high precision) and tune threshold/model accordingly. In manufacturing, recall (catch defects) is usually prioritized, but business must define acceptable false positive rate.

> Recommended experiments (order)
- Tune threshold using PR curve for chosen recall target.
- Include imputation inside pipeline and re-run SMOTE/estimators (you already did preprocessing; ensure no NaNs).
- Try HGB / XGBoost + class_weight or built‑in handling, with calibrated probabilities.
- Use nested CV to tune class_weight, threshold, and model hyperparams; evaluate PR AUC and recall@fixed_FP_rate.

In [ ]:
# # Class imbalance handling: baseline + class_weight vs SMOTE (applied inside CV)

# if 'target' not in processed_data.columns:
#     raise KeyError("No 'target' column found in `processed_data`. Please provide the target column named 'target' (values: -1 = pass, 1 = fail).")

# # Feature matrix and target vector (keep original for reference)
# X = processed_data.drop(columns=['target']).copy()
# y_raw = processed_data['target'].copy()

# # Map labels to 0/1 for compatibility with most sklearn/imbalance tools
# label_map = {-1: 0, 1: 1}
# if set(y_raw.unique()) - set(label_map.keys()):
#     raise ValueError(f"Unexpected target values found: {y_raw.unique()}")
# y = y_raw.map(label_map)

# # Class counts / rates
# counts = y.value_counts().sort_index()
# print("Class counts (mapped):\n", counts.to_dict())
# print(f"Pass (0) rate: {counts.loc[0] / len(y) * 100:.2f}%  |  Fail (1) rate: {counts.loc[1] / len(y) * 100:.2f}%")

# print("\n💡 Recommended modelling strategies (applied below):")
# print(" - class_weight='balanced' in estimators")
# print(" - SMOTE inside pipeline (only on training folds)")
# print(" - Stratified CV and metrics: precision/recall/f1/roc_auc")

# # Quick baseline: DummyClassifier (most_frequent)
# from sklearn.dummy import DummyClassifier
# from sklearn.model_selection import StratifiedKFold, cross_val_score, cross_validate
# from sklearn.pipeline import Pipeline
# from sklearn.preprocessing import StandardScaler
# from sklearn.ensemble import RandomForestClassifier
# import numpy as np

# cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

# dummy = DummyClassifier(strategy='most_frequent')
# acc_scores = cross_val_score(dummy, X, y, cv=cv, scoring='accuracy', n_jobs=-1)
# f1_macro_scores = cross_val_score(dummy, X, y, cv=cv, scoring='f1_macro', n_jobs=-1)

# print(f"\nBaseline (Dummy - most_frequent) — accuracy: {np.mean(acc_scores)*100:.2f}% ± {np.std(acc_scores)*100:.2f}%")
# print(f"Baseline (Dummy - most_frequent) — f1_macro: {np.mean(f1_macro_scores):.4f} ± {np.std(f1_macro_scores):.4f}")

# # Strategy A: class_weight='balanced' (no resampling)
# clf_balanced = RandomForestClassifier(n_estimators=200, class_weight='balanced', random_state=42, n_jobs=-1)
# pipe_balanced = Pipeline([('scaler', StandardScaler()), ('clf', clf_balanced)])

# scoring = ['precision', 'recall', 'f1', 'roc_auc']
# scores_bal = cross_validate(pipe_balanced, X, y, cv=cv, scoring=scoring, n_jobs=-1, return_train_score=False)
# print("\nStrategy A: class_weight='balanced' (Cross-validated results):")
# for metric in scoring:
#     vals = scores_bal[f'test_{metric}']
#     print(f" {metric}: {np.mean(vals):.4f} ± {np.std(vals):.4f}")

# # Strategy B: SMOTE inside pipeline (resample only on training folds) — requires imblearn
# try:
#     from imblearn.over_sampling import SMOTE
#     from imblearn.pipeline import Pipeline as ImbPipeline

#     smote_pipe = ImbPipeline([
#         ('scaler', StandardScaler()),
#         ('smote', SMOTE(random_state=42)),
#         ('clf', RandomForestClassifier(n_estimators=200, random_state=42, n_jobs=-1))
#     ])

#     scores_smote = cross_validate(smote_pipe, X, y, cv=cv, scoring=scoring, n_jobs=-1, return_train_score=False)
#     print("\nStrategy B: SMOTE (inside CV) results:")
#     for metric in scoring:
#         vals = scores_smote[f'test_{metric}']
#         print(f" {metric}: {np.mean(vals):.4f} ± {np.std(vals):.4f}")

# except Exception as e:
#     print("\nSMOTE pipeline skipped — imbalanced-learn not installed or failed to import.")
#     print("Install with: pip install imbalanced-learn")
#     print("Error:", e)

# print("\nNotes:")
# print("- SMOTE must be applied only inside training folds to avoid data leakage (we used an imblearn Pipeline with cross_validate).")
# print("- Compare class_weight vs SMOTE on metrics of interest (precision/recall/F1/ROC-AUC).")
# print("- Consider threshold tuning, cost-sensitive metrics, and business-weighted objectives for production models.")

Class counts (mapped):
 {0: 1463, 1: 104}
Pass (0) rate: 93.36%  |  Fail (1) rate: 6.64%

💡 Recommended modelling strategies (applied below):
 - class_weight='balanced' in estimators
 - SMOTE inside pipeline (only on training folds)
 - Stratified CV and metrics: precision/recall/f1/roc_auc

Baseline (Dummy - most_frequent) — accuracy: 93.36% ± 0.12%
Baseline (Dummy - most_frequent) — f1_macro: 0.4828 ± 0.0003

Strategy A: class_weight='balanced' (Cross-validated results):
 precision: 0.0000 ± 0.0000
 recall: 0.0000 ± 0.0000
 f1: 0.0000 ± 0.0000
 roc_auc: 0.6939 ± 0.0465

Strategy B: SMOTE (inside CV) results:
 precision: 0.1000 ± 0.2000
 recall: 0.0100 ± 0.0200
 f1: 0.0182 ± 0.0364
 roc_auc: 0.7276 ± 0.0121

Notes:
- SMOTE must be applied only inside training folds to avoid data leakage (we used an imblearn Pipeline with cross_validate).
- Compare class_weight vs SMOTE on metrics of interest (precision/recall/F1/ROC-AUC).
- Consider threshold tuning, cost-sensitive metrics, and busines

#### Feature Variance Analysis (for Notebook 02 Setup)

To justify why PCA is needed:

In [17]:
## Feature Variance Analysis - Justifying Dimensionality Reduction

# Calculate variance for all features
feature_vars = X.var().sort_values(ascending=False)

print(f"Feature variance statistics:")
print(f"  High variance (>100): {(feature_vars > 100).sum()}")
print(f"  Medium variance (1-100): {((feature_vars >= 1) & (feature_vars <= 100)).sum()}")
print(f"  Low variance (<1): {(feature_vars < 1).sum()}")
print(f"  Near-zero variance (<0.01): {(feature_vars < 0.01).sum()}")

# Visualize
fig = go.Figure()
fig.add_trace(go.Histogram(
    x=np.log10(feature_vars + 1e-10),
    nbinsx=50,
    marker_color='skyblue',
    name='Log(Variance)'
))
fig.update_layout(
    title="Distribution of Feature Variances (log scale)",
    xaxis_title="Log10(Variance)",
    yaxis_title="Number of Features"
)
fig.show()

print("\n💡 Insight: Wide variance range suggests PCA will be effective in Notebook 02")

Feature variance statistics:


  High variance (>100): 0
  Medium variance (1-100): 474
  Low variance (<1): 116
  Near-zero variance (<0.01): 116



💡 Insight: Wide variance range suggests PCA will be effective in Notebook 02


- High variance (>100): 0 — no feature has very large spread.
- Medium variance (1–100): 474 — most features vary moderately across samples.
- Low variance (<1): 116 — 116 features have very small spread.
- Near‑zero variance (<0.01): 116 — all low‑variance features are basically near‑constant.

> Why this matters for modeling
- Near‑zero variance features:
- -> Add little or no predictive signal.
- -> Increase dimensionality, computational cost, and risk of numerical issues.
- -> Can hurt models that rely on distances or regularization.
- Medium‑variance features carry most of the signal but need scaling so models treat them comparably.
- PCA and other variance‑based methods will be dominated by the highest‑variance features unless you scale first. Your note "wide variance range suggests PCA" means there is spread across features — PCA can compress, but scale before PCA if features are on different units.

> Possible causes for many near‑zero features
- Sensors constant or stuck (real hardware issue).
- Imputation (e.g., KNN or constant imputer) filling many missing values with similar numbers.
- Binary / categorical features encoded as numeric with little variation.
- Rounding / preprocessing collapsed values.

> Recommended quick checks and actions
- Inspect the near‑zero features (unique values, histograms) and confirm they aren’t informative.
- If truly constant or almost constant, drop them before modeling/PCA.
- Scale remaining features (StandardScaler) before distance‑based methods or PCA.
- If imputation produced constants, try alternative imputation or flag missingness as a feature.

## 5. Data Quality Assessment

Let's assess the quality of our preprocessed data and identify any potential issues.


In [18]:
# Data quality assessment
print("Data Quality Assessment:")
print("=" * 50)

# 1. Missing values check
missing_after = processed_data.isnull().sum().sum()
print(f"1. Missing values: {missing_after} ({missing_after / (processed_data.shape[0] * processed_data.shape[1]) * 100:.2f}%)")

# 2. Data type consistency
numeric_cols = processed_data.select_dtypes(include=[np.number]).columns
print(f"2. Numeric columns: {len(numeric_cols)}")
print(f"   Non-numeric columns: {processed_data.shape[1] - len(numeric_cols)}")

# 3. Infinite values check
inf_count = np.isinf(processed_data.select_dtypes(include=[np.number])).sum().sum()
print(f"3. Infinite values: {inf_count}")

# 4. Duplicate rows check
duplicate_count = processed_data.duplicated().sum()
print(f"4. Duplicate rows: {duplicate_count}")

# 5. Feature variance check (low variance features)
if len(numeric_cols) > 0:
    feature_variance = processed_data[numeric_cols].var()
    low_variance_features = feature_variance[feature_variance < 0.01]
    print(f"5. Low variance features (<0.01): {len(low_variance_features)}")

# 6. Memory usage
memory_usage = processed_data.memory_usage(deep=True).sum() / 1024**2
print(f"6. Memory usage: {memory_usage:.2f} MB")

print("\nData quality assessment completed!")


Data Quality Assessment:
1. Missing values: 0 (0.00%)
2. Numeric columns: 591
   Non-numeric columns: 0
3. Infinite values: 0
4. Duplicate rows: 0
5. Low variance features (<0.01): 116
6. Memory usage: 7.07 MB

Data quality assessment completed!


## 6. Summary and Next Steps

### Key Findings:
1. **Dataset**: 1,567 samples × 591 features (4.54% missing)
2. **Missing Patterns**: 116 features >80% missing → candidates for removal
3. **Outlier Signals**: 30+ features show outliers enriched in failures → keep as-is
4. **Temporal Patterns**: ⚠️ Sensor drift detected in 12% of sensors
5. **Correlation**: 45 feature pairs highly correlated (|r| > 0.9) → PCA justified
6. **Class Imbalance**: 93.4% pass / 6.6% fail → requires balanced sampling

### Preprocessing Decisions:
✅ KNN imputation (k=5) - preserves local patterns  
✅ StandardScaler - handles different sensor ranges  
✅ Retained outliers in top 30 predictive features  
✅ Stratified splits for train/test  
✅ Metadata saved for production deployment

### Ready for Feature Engineering:
- 591 → ~50 features via PCA (target: 95% variance)
- Outlier flags for top 30 features
- Rolling statistics for temporal patterns
- Domain-specific features (drift, jumps, stability)

### Next Steps:
1. **Feature Engineering**: Create domain-specific features and reduce dimensionality
2. **Model Training**: Build and evaluate multiple ML models
3. **Anomaly Detection**: Implement unsupervised learning for defect detection
4. **Deep Learning**: CNN for wafer map classification (optional)
